In [1]:
!pip install biopython

In [2]:
!pip install geoparse

In [3]:
!pip install geopandas

In [4]:
!pip install pyspark

In [1]:
import requests
from Bio import Entrez
import GEOparse
import os
import gzip
import shutil
import pandas as pd
from os.path import join
from collections import defaultdict
import numpy as np
import csv
import download_files
import polars as pl
import mysql.connector
from mysql.connector import errorcode

In [2]:
#disease names and ids 
diseases_tsv_file='../data/raw/data_01_neuro_diseases_final_disease_selected.tsv'
disease_names=download_files.extract_tsv(diseases_tsv_file)

In [3]:
#email and path to store the GDS files
email_request='l.masa@alumnos.upm.es'
gds_path="../data/gds"

In [ ]:
#query and download in the gds path
disease_gds_prefiltered = download_files.download_and_save_gds(email_request, disease_names,gds_path)
disease_gds_prefiltered

29-May-2024 10:08:57 DEBUG utils - Directory /home/lmasa/GEO_Laura/Data/gds already exists. Skipping.
29-May-2024 10:08:57 INFO GEOparse - Downloading ftp://ftp.ncbi.nlm.nih.gov/geo/datasets/GDS3nnn/GDS3864/soft/GDS3864.soft.gz to /home/lmasa/GEO_Laura/Data/gds/GDS3864.soft.gz
100%|██████████████████████████████████████████████████████████████████████████████████████████| 3.26M/3.26M [00:01<00:00, 1.71MB/s]
29-May-2024 10:09:00 DEBUG downloader - Size validation passed
29-May-2024 10:09:00 DEBUG downloader - Moving /tmp/tmp1n5w3mdb to /home/lmasa/GEO_Laura/Data/gds/GDS3864.soft.gz
29-May-2024 10:09:00 DEBUG downloader - Successfully downloaded ftp://ftp.ncbi.nlm.nih.gov/geo/datasets/GDS3nnn/GDS3864/soft/GDS3864.soft.gz
29-May-2024 10:09:00 INFO GEOparse - Parsing /home/lmasa/GEO_Laura/Data/gds/GDS3864.soft.gz: 
29-May-2024 10:09:00 DEBUG GEOparse - DATABASE: Geo
29-May-2024 10:09:00 DEBUG GEOparse - DATASET: GDS3864
29-May-2024 10:09:00 DEBUG GEOparse - SUBSET: GDS3864_1
29-May-2024 10

In [ ]:
#download the disease and GDS relation before filtering
disease_gds_prefiltered.to_csv('../results/prefilt_disease_gds.csv',index=False)

In [5]:
#decompress gds files
download_files.decompress_gds_gz_files(gds_path)

In [16]:
#read the disease and GDS relation before filtering
disease_gds_prefiltered=pd.read_csv('../results/prefilt_disease_gds.csv')

In [14]:
#filter the GDS by specific criteria 
diseases_gds_filtered=download_files.filter_gds(gds_path, disease_gds_prefiltered)
disease_gds_filtered.to_csv('../results/disease_gds.csv',index=False)

30-Jun-2024 14:13:36 INFO GEOparse - Parsing ../data/gds/GDS1050.soft: 
30-Jun-2024 14:13:36 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 14:13:36 DEBUG GEOparse - DATASET: GDS1050
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS1050_1
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS1050_2
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS1050_3
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS1050_4
30-Jun-2024 14:13:36 DEBUG GEOparse - DATASET: GDS1050
30-Jun-2024 14:13:36 INFO GEOparse - Parsing ../data/gds/GDS4136.soft: 
30-Jun-2024 14:13:36 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 14:13:36 DEBUG GEOparse - DATASET: GDS4136
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS4136_1
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS4136_2
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS4136_3
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS4136_4
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS4136_5
30-Jun-2024 14:13:36 DEBUG GEOparse - SUBSET: GDS4136_6
30-Jun-2024 14:13:36 DEBUG 

In [4]:
disease_gds_filtered=pd.read_csv('../results/disease_gds.csv')

In [8]:
#remove the GDS that do not accomplish the criteria
gds_ids = disease_gds_filtered['gds_id'].tolist()
for filename in os.listdir(gds_path):
    if filename.startswith("GDS") and filename.endswith(".soft"):
        gds_id = filename.split(".")[0]  # get the GDS id of each file
        if gds_id not in gds_ids:
            file_path = os.path.join(gds_path, filename)
            os.remove(file_path)

In [6]:
gpl_path="../data/gpl"

In [4]:
#Get the GDS-GPL relation
gds_gpl_mapping=download_files.create_gds_gpl_mapping_and_download(gds_path,gpl_path)

30-Jun-2024 13:39:04 INFO GEOparse - Parsing ../data/gds/GDS1050.soft: 
30-Jun-2024 13:39:04 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 13:39:04 DEBUG GEOparse - DATASET: GDS1050
30-Jun-2024 13:39:04 DEBUG GEOparse - SUBSET: GDS1050_1
30-Jun-2024 13:39:04 DEBUG GEOparse - SUBSET: GDS1050_2
30-Jun-2024 13:39:04 DEBUG GEOparse - SUBSET: GDS1050_3
30-Jun-2024 13:39:04 DEBUG GEOparse - SUBSET: GDS1050_4
30-Jun-2024 13:39:04 DEBUG GEOparse - DATASET: GDS1050
30-Jun-2024 13:39:04 DEBUG utils - Directory /home/lmasa/GEO_Laura/data/gpl already exists. Skipping.
30-Jun-2024 13:39:04 INFO GEOparse - File already exist: using local version.
30-Jun-2024 13:39:04 INFO GEOparse - Parsing /home/lmasa/GEO_Laura/data/gpl/GPL96.annot.gz: 
30-Jun-2024 13:39:04 DEBUG GEOparse - ANNOTATION: 
30-Jun-2024 13:39:04 INFO GEOparse - Parsing ../data/gds/GDS4136.soft: 
30-Jun-2024 13:39:04 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 13:39:04 DEBUG GEOparse - DATASET: GDS4136
30-Jun-2024 13:39:04 DEBUG GEOparse - S

Downloaded GPL GPL96 for GDS GDS1050 to /home/lmasa/GEO_Laura/data/gpl/GPL96


30-Jun-2024 13:39:04 DEBUG utils - Directory /home/lmasa/GEO_Laura/data/gpl already exists. Skipping.
30-Jun-2024 13:39:04 INFO GEOparse - File already exist: using local version.
30-Jun-2024 13:39:04 INFO GEOparse - Parsing /home/lmasa/GEO_Laura/data/gpl/GPL570.annot.gz: 
30-Jun-2024 13:39:04 DEBUG GEOparse - ANNOTATION: 
/home/lmasa/miniconda3/lib/python3.12/site-packages/GEOparse/GEOparse.py:401: DtypeWarning: Columns (12) have mixed types. Specify dtype option on import or set low_memory=False.
  return read_csv(StringIO(data), index_col=None, sep="\t")
30-Jun-2024 13:39:05 INFO GEOparse - Parsing ../data/gds/GDS4150.soft: 
30-Jun-2024 13:39:05 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 13:39:05 DEBUG GEOparse - DATASET: GDS4150
30-Jun-2024 13:39:05 DEBUG GEOparse - SUBSET: GDS4150_1
30-Jun-2024 13:39:05 DEBUG GEOparse - SUBSET: GDS4150_2
30-Jun-2024 13:39:05 DEBUG GEOparse - SUBSET: GDS4150_3
30-Jun-2024 13:39:05 DEBUG GEOparse - SUBSET: GDS4150_4
30-Jun-2024 13:39:05 DEBUG GEOpar

Downloaded GPL GPL570 for GDS GDS4136 to /home/lmasa/GEO_Laura/data/gpl/GPL570


/home/lmasa/miniconda3/lib/python3.12/site-packages/GEOparse/GEOparse.py:401: DtypeWarning: Columns (12) have mixed types. Specify dtype option on import or set low_memory=False.
  return read_csv(StringIO(data), index_col=None, sep="\t")
30-Jun-2024 13:39:06 INFO GEOparse - Parsing ../data/gds/GDS563.soft: 
30-Jun-2024 13:39:06 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 13:39:06 DEBUG GEOparse - DATASET: GDS563
30-Jun-2024 13:39:06 DEBUG GEOparse - SUBSET: GDS563_1
30-Jun-2024 13:39:06 DEBUG GEOparse - SUBSET: GDS563_2
30-Jun-2024 13:39:06 DEBUG GEOparse - DATASET: GDS563
30-Jun-2024 13:39:06 DEBUG utils - Directory /home/lmasa/GEO_Laura/data/gpl already exists. Skipping.
30-Jun-2024 13:39:06 INFO GEOparse - File already exist: using local version.
30-Jun-2024 13:39:06 INFO GEOparse - Parsing /home/lmasa/GEO_Laura/data/gpl/GPL8300.annot.gz: 
30-Jun-2024 13:39:06 DEBUG GEOparse - ANNOTATION: 


...

Downloaded GPL GPL570 for GDS GDS4854 to /home/lmasa/GEO_Laura/data/gpl/GPL570


/home/lmasa/miniconda3/lib/python3.12/site-packages/GEOparse/GEOparse.py:401: DtypeWarning: Columns (12) have mixed types. Specify dtype option on import or set low_memory=False.
  return read_csv(StringIO(data), index_col=None, sep="\t")
30-Jun-2024 13:39:34 INFO GEOparse - Parsing ../data/gds/GDS412.soft: 
30-Jun-2024 13:39:34 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 13:39:34 DEBUG GEOparse - DATASET: GDS412
30-Jun-2024 13:39:34 DEBUG GEOparse - SUBSET: GDS412_1
30-Jun-2024 13:39:34 DEBUG GEOparse - SUBSET: GDS412_2
30-Jun-2024 13:39:34 DEBUG GEOparse - SUBSET: GDS412_3
30-Jun-2024 13:39:34 DEBUG GEOparse - DATASET: GDS412
30-Jun-2024 13:39:34 DEBUG utils - Directory /home/lmasa/GEO_Laura/data/gpl already exists. Skipping.
30-Jun-2024 13:39:34 INFO GEOparse - File already exist: using local version.
30-Jun-2024 13:39:34 INFO GEOparse - Parsing /home/lmasa/GEO_Laura/data/gpl/GPL80.annot.gz: 
30-Jun-2024 13:39:34 DEBUG GEOparse - ANNOTATION: 
30-Jun-2024 13:39:34 INFO GEOparse - Pars

Downloaded GPL GPL570 for GDS GDS4218 to /home/lmasa/GEO_Laura/data/gpl/GPL570
Downloaded GPL GPL80 for GDS GDS412 to /home/lmasa/GEO_Laura/data/gpl/GPL80


30-Jun-2024 13:39:34 DEBUG utils - Directory /home/lmasa/GEO_Laura/data/gpl already exists. Skipping.
30-Jun-2024 13:39:34 INFO GEOparse - File already exist: using local version.
30-Jun-2024 13:39:34 INFO GEOparse - Parsing /home/lmasa/GEO_Laura/data/gpl/GPL570.annot.gz: 
30-Jun-2024 13:39:34 DEBUG GEOparse - ANNOTATION: 
/home/lmasa/miniconda3/lib/python3.12/site-packages/GEOparse/GEOparse.py:401: DtypeWarning: Columns (12) have mixed types. Specify dtype option on import or set low_memory=False.
  return read_csv(StringIO(data), index_col=None, sep="\t")
30-Jun-2024 13:39:35 INFO GEOparse - Parsing ../data/gds/GDS262.soft: 
30-Jun-2024 13:39:35 DEBUG GEOparse - DATABASE: Geo
30-Jun-2024 13:39:35 DEBUG GEOparse - DATASET: GDS262
30-Jun-2024 13:39:35 DEBUG GEOparse - SUBSET: GDS262_1
30-Jun-2024 13:39:35 DEBUG GEOparse - SUBSET: GDS262_2
30-Jun-2024 13:39:35 DEBUG GEOparse - SUBSET: GDS262_3
30-Jun-2024 13:39:35 DEBUG GEOparse - SUBSET: GDS262_4
30-Jun-2024 13:39:35 DEBUG GEOparse - S

Downloaded GPL GPL570 for GDS GDS4522 to /home/lmasa/GEO_Laura/data/gpl/GPL570
Downloaded GPL GPL91 for GDS GDS262 to /home/lmasa/GEO_Laura/data/gpl/GPL91


In [31]:
gds_gpl_mapping.to_csv('../results/gds_gpl.csv',index=False)

In [7]:
#decompress the GPL files
download_files.decompress_gpl_gz_files(gpl_path)

In [12]:
disease_gds_filtered=pd.read_csv('../results/disease_gds.csv')
disease_gds_prefiltered=pd.read_csv('../results/prefilt_disease_gds.csv')

In [13]:
different_counts=disease_gds_prefiltered.nunique()
for column, count in different_counts.items():
    print(f'The number of different {column} is {count}')

The number of different disease_id is 80
The number of different gds_id is 134


In [14]:
different_counts_filt=diseases_gds_filtered.nunique()
for column, count in different_counts_filt.items():
    print(f'The number of different {column} is {count}')

The number of different disease_id is 63
The number of different gds_id is 73
